In [1]:

import psycopg2

In [2]:
import requests #for rotated proxies
from bs4 import BeautifulSoup

base_url = 'https://www.nekretnine.rs';

In [3]:
#funkcije za parsiranje informacija koje su potrebne za pretrazivanje objekata na sajtu

def parse_transakcija (podaci):
    for elem in podaci:
        if elem.contents[0].strip()== "Transakcija:":
            try:
                return elem.contents[1].text.strip()
            except Exception:
                return None
    return None

def parse_kategorija (podaci):
    for elem in podaci:
        if elem.contents[0].strip()=="Kategorija:":
            try:
                return elem.contents[1].text.strip().rsplit(' ',1)[1]
            except Exception:
                return None
    return None
    
def parse_kvadratura (podaci):
    for elem in podaci:
        if elem.contents[0].strip()== "Kvadratura:":
            try:
                return elem.contents[1].text.strip()
            except Exception:
                return None
    return None
    
def parse_stanje (podaci):
    for elem in podaci:
        if elem.contents[0].strip()== "Stanje nekretnine:":
            try:
                return elem.contents[1].text.strip()
            except Exception:
                return None
            
    return None

def parse_broj_soba (podaci):
    for elem in podaci:
        if elem.contents[0].strip()== "Ukupan broj soba:":
            try:
                return int(elem.contents[1].text.strip())
            except Exception:
                return None
    return None

def parse_broj_kupatila (podaci):
    for elem in podaci:
        if elem.contents[0].strip()== "Broj kupatila:":
            try:
                return int(elem.contents[1].text.strip())
            except Exception:
                return None
    return None

def parse_uknjizeno (podaci):
    for elem in podaci:
        if elem.contents[0].strip()== "Uknjiženo:":
            try:
                return elem.contents[1].text.strip()
            except Exception:
                return None
    return None

def parse_godina_izgradnje (podaci):
    for elem in podaci:
        if elem.contents[0].strip()== "Godina izgradnje:":
            try:
                return int(elem.contents[1].text.strip())
            except Exception:
                return None
    return None

def parse_spratnost (podaci):
    for elem in podaci:
        if elem.contents[0].strip()== "Spratnost:":
            try:
                return elem.contents[1].text.strip()
            except Exception:
                return None
    return None

def parse_ukupno_spratova (podaci):
    for elem in podaci:
        if elem.contents[0].strip()== "Ukupan broj spratova:":
            try:
                return int(elem.contents[1].text.strip())
            except Exception:
                return None
    return None

def parse_povrsina_zemljista (podaci):
    for elem in podaci:
        if elem.contents[0].strip()== "Površina zemljišta:":
            try:
                return elem.contents[1].text.strip()
            except Exception:
                return None
    return None

def has (dodatno, option): 
    try:
        opcije_dodatne_objects = dodatno.findAll("ul")[0].findChildren("li")
        opcije_dodatne = []
        for opcija in opcije_dodatne_objects:
            opcije_dodatne.append(opcija.text)
        return option in opcije_dodatne
    except Exception:
        return False

def parse_grad(lokacija_div):
    try:
        lokacija_ul = lokacija_div.findAll("ul")[0].findChildren("li")
        grad = lokacija_ul[2].text.strip()
        return grad
    except Exception:
        return None
    
def parse_mesto(lokacija_div):
    try:
        lokacija_ul = lokacija_div.findAll("ul")[0].findChildren("li")
        mesto = lokacija_ul[3].text.strip()
        return mesto
    except Exception:
        return None
    
def parse_grejanje(ostalo):
    try:
        ostalo_ul = ostalo.findAll("ul")[0].findChildren("li")
        for el in ostalo_ul:
            if el.contents[0].find("Grejanje")>0 :
                return el.contents[0].strip()[9:].strip()
    except Exception:
        return None
    
def get_property(properties, type):
    try:
        for p in properties:
            h3 = p.findChildren("h3", recursive=False)
            if h3[0].text == type:
                return p
        return None
    except Exception:
        return None
            
    

def parseObject(object_url):
    url = base_url + object_url;
    print(url)
    page = requests.get(url)
    soup = BeautifulSoup(page.content, "html.parser")
    detalji = soup.find(id="detalji")
    property_emanities = detalji.findChildren("div", recursive=False)
    podaci = get_property(property_emanities, "Podaci o nekretnini")
    podaci_lista = podaci.find("ul")
    podaci_lista_elem = podaci_lista.findChildren("li")
    
    dodatna_opremljenost = get_property(property_emanities, "Dodatna opremljenost")
    ostalo = get_property(property_emanities, "Ostalo")
    
    #transakcija, kategorija, kvadratura, stanje, broj_soba string ili int
    transakcija = parse_transakcija (podaci_lista_elem)
    kategorija = parse_kategorija (podaci_lista_elem)
    kvadratura = parse_kvadratura (podaci_lista_elem)
    stanje = parse_stanje (podaci_lista_elem)
    broj_soba = parse_broj_soba (podaci_lista_elem)
    broj_kupatila = parse_broj_kupatila(podaci_lista_elem)
    uknjizeno = parse_uknjizeno(podaci_lista_elem)
    spratnost = parse_spratnost(podaci_lista_elem)
    ukupan_broj_spratova = parse_ukupno_spratova(podaci_lista_elem)
    povrsina_zemljista = parse_povrsina_zemljista(podaci_lista_elem)
    godina_izgradnje = parse_povrsina_zemljista(podaci_lista_elem)
    
    print(transakcija)
    print(kategorija)
    print(kvadratura)
    print(stanje)
    print(broj_soba)
    print(broj_kupatila)
    print(uknjizeno)
    print(spratnost)
    print(ukupan_broj_spratova)
    print(povrsina_zemljista)
    print(godina_izgradnje)
    
    
    #garaza, lift, terasa true/false
    garaza = has (dodatna_opremljenost, "Garaža")
    lift = has (dodatna_opremljenost, "Lift")
    terasa = has (dodatna_opremljenost, "Terasa")
    balkon = has (dodatna_opremljenost, "Balkon")
    
    print(garaza)
    print(lift)
    print(terasa)
    print(balkon)
    
    #tip grejanja string
    grejanje = parse_grejanje(ostalo)

    print(grejanje)
    
    #lokacija format: grad,mesto
    lokacija_div = soup.find("div", {"class":"property__location"})
    grad = parse_grad(lokacija_div) #prosledjujem div sa ul listom informacija o lokaciji
    mesto = parse_mesto(lokacija_div) #prosledjujem div  sa ul listom informacija o lokaciji
    print(grad)
    print(mesto)
    
    
    #dodaj element u bazu
    try:
        conn = psycopg2.connect(database='nekretnine_database', user='postgres', password = '1234', host='localhost', port=5432)
        cursor = conn.cursor()
        
        postgres_insert_query = """insert into nekretnine_info (kategorija, transakcija, lokacija, godina, povrsina_zemljista, ukupan_broj_spratova, uknjizeno, grejanje, broj_soba, broj_kupatila, terasa, balkon, kvadratura, spratnost, grad, url) values(%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s,%s, %s, %s);"""    
        record_to_insert = (kategorija, transakcija, mesto, godina_izgradnje, povrsina_zemljista, ukupan_broj_spratova, uknjizeno, grejanje, broj_soba, broj_kupatila, terasa, balkon, kvadratura, spratnost, grad, url)
        cursor.execute(postgres_insert_query, record_to_insert)
        
        conn.commit()
        count = cursor.rowcount
        print(count, "Uspesno insertovan red u bazi")
    except (Exception, psycopg2.Error) as error:
        print("neuspesno dodavanje u bazu", error)
    finally:
        if conn:
            cursor.close()
            conn.close()
            print("POSTGRESQL konekcija zatvorena")

In [4]:
#Zadatak 1. Pretraziti odgovarajuci sajt, prikazati realizovanu relacionu bazu podataka popunjenu trazenim podacima o nekretninama
URL = 'https://www.nekretnine.rs/stambeni-objekti/izdavanje-prodaja/izdavanje/lista/po-stranici/10/stranica/1';
import time
broj_stranica = 200
linkovi = [
    'https://www.nekretnine.rs/stambeni-objekti/stanovi/izdavanje-prodaja/izdavanje/lista/po-stranici/20/stranica/',
    'https://www.nekretnine.rs/stambeni-objekti/stanovi/izdavanje-prodaja/prodaja/lista/po-stranici/20/stranica/',
    'https://www.nekretnine.rs/stambeni-objekti/kuce/lista/po-stranici/20/stranica/'
]

page = requests.get(URL)
soup = BeautifulSoup(page.content, "html.parser")
objects = soup.find_all("div", class_="placehodler-preview-box")
objects_urls = []
for object in objects:
    objects_urls.append(object.findChildren("a", recursive=False)[0]["href"])



#for link in linkovi:
    #for strana in range(broj_stranica):
        #link_obrada = link + str(strana+1)
        #print("Trenutno obradjena strana: " + link_obrada)
        #try: 
            #time.sleep(3)
            #page = requests.get(URL)

            #soup = BeautifulSoup(page.content, "html.parser")
            #objects = soup.find_all("div", class_='placeholder-preview-box')
            #objects_urls = []
            #for object in objects:
                #objects_urls.append(object.findChildren("a", recursive=False)[0]["href"])

            #for url in objects_urls:
                #parseObject(url)
        #except Exception as e :
            #print("Greska u parsiranju linkova")
            #print(e)
            #continue

Trenutno obradjena strana: https://www.nekretnine.rs/stambeni-objekti/stanovi/izdavanje-prodaja/izdavanje/lista/po-stranici/20/stranica/1
https://www.nekretnine.rs/stambeni-objekti/stanovi/izdavanje-luksuznih-stanova-skyline--20--garaza/NkuoilUSFZL/
Izdavanje
stan
65 m²
Novogradnja
2
1
Da
4
None
None
None
True
True
True
False
Centralno grejanje
Beograd
Kneza Miloša ( centar )
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/knez-miletina-10-28m2-lux-novo-bajlonijeva-pijaca-dorcol-/NkiMVnbo5AH/
Izdavanje
stan
28 m²
Kompletna rekonstrukcija
2
2
Da
Visoko prizemlje
1
None
None
False
False
False
False
Etažno grejanje na struju
Beograd
Bajlonijeva pijaca
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/novi-beograd-blok-30-b92-bulevar-mihajla-pupina-25-73m2-650-eur/579490/
Izdavanje
stan
73 m²
Standardna gradnja
3
None
None
4
None
None
None
True
True
True
False
C

Izdavanje
stan
72 m²
Standardna gradnja
3
1
None
5
None
None
None
False
True
True
False
Centralno grejanje, Klima uređaj
Novi Sad
Liman 1
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/3-soban-lux-68-m2-laze-kostica-1sprat-useljiv-od-192021-id752/Nkynr4JSaPL/
Izdavanje
stan
68 m²
Novogradnja
3
1
None
1
None
None
None
False
True
True
False
Centralno grejanje, Klima uređaj
Novi Sad
Centar
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/dimitrija-tucovica-25-novogradnja-id-2932/NkxMS-UHxbE/
Izdavanje
stan
62 m²
Novogradnja
3
None
None
Visoko prizemlje
None
None
None
False
False
True
False
Centralno grejanje
Beograd
Zvezdara
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/izdavanje-luksuznih-stanova--30-gundulicev-venac-sajkaska/NkvZo21fDF8/
Izdavanje
stan
67 m²
Standardna gradnja
3
2
Da
9
None

Izdavanje
kuća
220 m²
Novogradnja
5
1
None
1
None
None
None
True
False
True
False
Centralno grejanje, Klima uređaj
Beograd
Novi Beograd Blok 7 (Paviljoni)
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/hotel-yu-40-lux-renoviran-id12539/NkOgMS4MpeF/
Izdavanje
stan
95 m²
Standardna gradnja
4
1
None
None
None
None
None
False
True
True
False
Centralno grejanje, Klima uređaj
Beograd
Novi Beograd Blok 11 (Hotel Jugoslavija)
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/izdavanje-luksuznih-stanova--20--garaza-vojvode-supljikca/Nk0otAyXv_Q/
Izdavanje
stan
57 m²
Novogradnja
2
1
Da
3
None
None
None
True
True
True
False
Centralno grejanje
Beograd
Crveni krst
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/slavija-kod-hrama-trosoban-id11895/NkC029M2e7i/
Izdavanje
stan
68 m²
Standardna gradnja
3
1
Non

Izdavanje
stan
57 m²
Novogradnja
2
1
None
3
None
None
None
False
True
True
False
Centralno grejanje, Klima uređaj
Beograd
Novi Beograd Blok 11 (Hotel Jugoslavija)
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
Trenutno obradjena strana: https://www.nekretnine.rs/stambeni-objekti/stanovi/izdavanje-prodaja/izdavanje/lista/po-stranici/20/stranica/5
https://www.nekretnine.rs/stambeni-objekti/stanovi/izdavanje-luksuznih-stanova-skyline--20--garaza/NkuoilUSFZL/
Izdavanje
stan
65 m²
Novogradnja
2
1
Da
4
None
None
None
True
True
True
False
Centralno grejanje
Beograd
Kneza Miloša ( centar )
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/knez-miletina-10-28m2-lux-novo-bajlonijeva-pijaca-dorcol-/NkiMVnbo5AH/
Izdavanje
stan
28 m²
Kompletna rekonstrukcija
2
2
Da
Visoko prizemlje
1
None
None
False
False
False
False
Etažno grejanje na struju
Beograd
Bajlonijeva pijaca
1 Uspesno insertovan red u bazi
POSTGRESQL konekcij

Izdavanje
stan
44 m²
Novogradnja
2
None
None
Visoko prizemlje
6
None
None
True
True
False
False
Centralno grejanje
Beograd
Đeram pijaca
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/25-soban-72-m2-liman-1-jiricekova-5sprat-lift-id1311/NkCM8Y90Drx/
Izdavanje
stan
72 m²
Standardna gradnja
3
1
None
5
None
None
None
False
True
True
False
Centralno grejanje, Klima uređaj
Novi Sad
Liman 1
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/3-soban-lux-68-m2-laze-kostica-1sprat-useljiv-od-192021-id752/Nkynr4JSaPL/
Izdavanje
stan
68 m²
Novogradnja
3
1
None
1
None
None
None
False
True
True
False
Centralno grejanje, Klima uređaj
Novi Sad
Centar
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/dimitrija-tucovica-25-novogradnja-id-2932/NkxMS-UHxbE/
Izdavanje
stan
62 m²
Novogradnja
3
None
None
Visoko prizem

...

Izdavanje
stan
65 m²
Novogradnja
2
1
Da
4
None
None
None
True
True
True
False
Centralno grejanje
Beograd
Kneza Miloša ( centar )
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/knez-miletina-10-28m2-lux-novo-bajlonijeva-pijaca-dorcol-/NkiMVnbo5AH/
Izdavanje
stan
28 m²
Kompletna rekonstrukcija
2
2
Da
Visoko prizemlje
1
None
None
False
False
False
False
Etažno grejanje na struju
Beograd
Bajlonijeva pijaca
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/novi-beograd-blok-30-b92-bulevar-mihajla-pupina-25-73m2-650-eur/579490/
Izdavanje
stan
73 m²
Standardna gradnja
3
None
None
4
None
None
None
True
True
True
False
Centralno grejanje
Beograd
Novi Beograd Blok 30 (B92)
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/2-soban-50-m2-park-city-6sprat-ul-narodnog-fronta-id1175/Nku2o1qKlZS/
Izdavanje
sta

Izdavanje
stan
68 m²
Novogradnja
3
1
None
1
None
None
None
False
True
True
False
Centralno grejanje, Klima uređaj
Novi Sad
Centar
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/dimitrija-tucovica-25-novogradnja-id-2932/NkxMS-UHxbE/
Izdavanje
stan
62 m²
Novogradnja
3
None
None
Visoko prizemlje
None
None
None
False
False
True
False
Centralno grejanje
Beograd
Zvezdara
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/izdavanje-luksuznih-stanova--30-gundulicev-venac-sajkaska/NkvZo21fDF8/
Izdavanje
stan
67 m²
Standardna gradnja
3
2
Da
9
None
None
None
False
True
True
False
None
Beograd
Gundulićev venac
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/izdavanje-luksuznih-stanova--20--garaza-vojvode-supljikca/Nk0otAyXv_Q/
Izdavanje
stan
57 m²
Novogradnja
2
1
Da
3
None
None
None
True
True
True
False
C

Izdavanje
stan
52 m²
Novogradnja
2
1
Da
1
None
None
None
True
True
True
False
Centralno grejanje
Beograd
Vračar (Hram)
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/hram-svetog-save-20-namesten-id12847/NkZE_mYhIFP/
Izdavanje
stan
55 m²
Standardna gradnja
2
1
None
2
None
None
None
False
False
False
False
Klima uređaj, Etažno grejanje na gas
Beograd
Vračar (Hram)
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/kalenic-pijaca-20-namesten-id12846/Nkfevsfo00L/
Izdavanje
stan
57 m²
Novogradnja
2
1
None
3
None
None
None
True
True
True
False
Centralno grejanje, Klima uređaj
Beograd
Kalenić pijaca
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/izdavanje-luksuznih-stanova-novi-dorcol--20--venizelosova/Nk-vcftkjPU/
Izdavanje
stan
42 m²
Novogradnja
2
1
Da
1
None
None
None
True
True
True
False
Central

Izdavanje
stan
65 m²
Novogradnja
2
1
Da
4
None
None
None
True
True
True
False
Centralno grejanje
Beograd
Kneza Miloša ( centar )
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/knez-miletina-10-28m2-lux-novo-bajlonijeva-pijaca-dorcol-/NkiMVnbo5AH/
Izdavanje
stan
28 m²
Kompletna rekonstrukcija
2
2
Da
Visoko prizemlje
1
None
None
False
False
False
False
Etažno grejanje na struju
Beograd
Bajlonijeva pijaca
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/novi-beograd-blok-30-b92-bulevar-mihajla-pupina-25-73m2-650-eur/579490/
Izdavanje
stan
73 m²
Standardna gradnja
3
None
None
4
None
None
None
True
True
True
False
Centralno grejanje
Beograd
Novi Beograd Blok 30 (B92)
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/2-soban-50-m2-park-city-6sprat-ul-narodnog-fronta-id1175/Nku2o1qKlZS/
Izdavanje
sta

Izdavanje
stan
68 m²
Novogradnja
3
1
None
1
None
None
None
False
True
True
False
Centralno grejanje, Klima uređaj
Novi Sad
Centar
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/dimitrija-tucovica-25-novogradnja-id-2932/NkxMS-UHxbE/
Izdavanje
stan
62 m²
Novogradnja
3
None
None
Visoko prizemlje
None
None
None
False
False
True
False
Centralno grejanje
Beograd
Zvezdara
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/izdavanje-luksuznih-stanova--30-gundulicev-venac-sajkaska/NkvZo21fDF8/
Izdavanje
stan
67 m²
Standardna gradnja
3
2
Da
9
None
None
None
False
True
True
False
None
Beograd
Gundulićev venac
1 Uspesno insertovan red u bazi
POSTGRESQL konekcija zatvorena
https://www.nekretnine.rs/stambeni-objekti/stanovi/izdavanje-luksuznih-stanova--20--garaza-vojvode-supljikca/Nk0otAyXv_Q/
Izdavanje
stan
57 m²
Novogradnja
2
1
Da
3
None
None
None
True
True
True
False
C

In [5]:
#moj_objekat = objects_urls[0]
#parseObject(moj_objekat)